<a href="https://www.kaggle.com/code/saisanjaykottakota/animal-prediction-yolov8n-ddp?scriptVersionId=186588001" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
!nvidia-smi

Tue Jul  2 20:44:31 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.129.03             Driver Version: 535.129.03   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   43C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [2]:
!pip install uv

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 2.1 MB/s eta 0:00:00


In [3]:
!uv pip install --system  ultralytics  --upgrade

Resolved 51 packages in 1.17s
⠙ Preparing packages... (0/39)
⠙ Preparing packages... (0/39)
pandas     ------------------------------     0 B/13.03 MB
⠙ Preparing packages... (0/39)
matplotlib ------------------------------     0 B/8.30 MB
pandas     ------------------------------     0 B/13.03 MB
⠙ Preparing packages... (0/39)
matplotlib ------------------------------ 1.38 kB/8.30 MB
pandas     ------------------------------     0 B/13.03 MB
⠙ Preparing packages... (0/39)
fonttools  ------------------------------     0 B/4.62 MB
matplotlib ------------------------------ 1.38 kB/8.30 MB
pandas     ------------------------------     0 B/13.03 MB
⠙ Preparing packages... (0/39)
fonttools  ------------------------------     0 B/4.62 MB
matplotlib ------------------------------ 1.38 kB/8.30 MB
pandas     ------------------------------     0 B/13.03 MB
opencv-python ------------------------------     0 B/62.55 MB
⠙ Preparing packages... (0/39)
fonttools  ------------------------------     0 

In [4]:
# !pip install torch

In [5]:
import os
import random
import shutil
from collections import defaultdict, Counter
from pathlib import Path
from typing import Dict, List, Tuple, Optional, Iterable
import yaml

import cv2
import plotly.express as px
from plotly import subplots
from tqdm.notebook import tqdm
import torch
from ultralytics import YOLO

In [6]:
# DATASET_PATH = '/kaggle/input/poaching-and-animal-detection-dataset'  # Path to source dataset
# MASTER_PATH = '/kaggle/working/' # Path where all outputs are stored (intermediate and final)
DATASET_PATH = '/kaggle/input/Project Dataset for Animal Prediction'  # Path to source dataset
MASTER_PATH = '/kaggle/working/' # Path where all outputs are stored (intermediate and final)
DEBUG = False # Activete to run notebook faster
CPU = False

if not CPU:
    assert torch.cuda.is_available(), 'CUDA not found!'

In [7]:
!ls "/kaggle/input/Project Dataset for Animal Prediction"

test  train


In [8]:
import os
import random
import shutil
from collections import defaultdict, Counter
from pathlib import Path
from tqdm import tqdm
from typing import Dict, List, Optional, Tuple
import cv2
import yaml  # Ensure PyYAML is installed

# Type aliases
DatasetIndex = Dict[str, Dict[str, List[str]]]
DatasetStats = Dict[str, int]

# LookupTable class definition
class LookupTable:
    def __init__(self, add_unknown_token=True):
        self.add_unknown_token = add_unknown_token
        self.table = {}
        self.inverse_table = {}
        if add_unknown_token:
            self.add('<unknown>')

    def add(self, item):
        if item not in self.table:
            index = len(self.table)
            self.table[item] = index
            self.inverse_table[index] = item

    def __getitem__(self, item):
        if self.add_unknown_token:
            return self.table.get(item, self.table['<unknown>'])
        return self.table[item]

    def __len__(self):
        return len(self.table)

    def __iter__(self):
        return iter(self.table)

# AnimalToYOLODatasetAdapter class definition
class AnimalToYOLODatasetAdapter:

    def __init__(self, path: str, label_filter: Optional[List[str]] = None):
        self._path = path
        self._index, self.label_stats, self.split_stats, self.label_lookup, self._size = \
            self._index_dataset(path, label_filter)

    @staticmethod
    def _index_dataset(path: str, label_filter: Optional[List[str]] = None) \
        -> Tuple[DatasetIndex, DatasetStats, DatasetStats, LookupTable, int]:

        index: DatasetIndex = defaultdict(dict)
        label_stats: DatasetStats = Counter()
        split_stats: DatasetStats = Counter()
        lookup = LookupTable(add_unknown_token=False)
        size = 0

        splits = os.listdir(path)
        for split in splits:
            split_path = os.path.join(path, split)
            if not os.path.isdir(split_path):
                continue
            labels = os.listdir(split_path)
            for label in tqdm(labels, desc=f'Indexing {split}', unit='sample'):
                if label_filter is not None and label not in label_filter:
                    continue

                label_path = os.path.join(split_path, label)
                sample_ids = [Path(filename).stem for filename in os.listdir(label_path)
                              if filename != 'Label' and (filename.endswith('.jpg') or filename.endswith('.jpeg'))]
                annotations_path = os.path.join(label_path, 'Label')
                if not os.path.exists(annotations_path):
                    continue
                annot_sample_ids = [Path(filename).stem for filename in os.listdir(annotations_path)
                                    if filename.endswith('.txt')]
                assert set(sample_ids) == set(annot_sample_ids), 'Image sample ids and annotation sample ids do not match'

                # Update index, stats and lookup
                index[split][label] = sample_ids

                n_samples = len(sample_ids)
                label_stats[label] += n_samples
                split_stats[split] += n_samples
                size += n_samples

                lookup.add(label)

        return dict(index), dict(label_stats), dict(split_stats), lookup, size

    def __len__(self) -> int:
        return self._size

    @property
    def labels(self) -> List[str]:
        return list(self.label_lookup)

    @property
    def n_labels(self) -> int:
        return len(self.label_lookup)

    def get_random_samples(self, n: int, split: str = 'train') -> List[Tuple[str, str, str]]:
        split_index = self._index.get(split, {})
        if not split_index:
            raise ValueError(f'Split "{split}" not found in the dataset.')
        label_names = self.labels

        result: List[Tuple[str, str, str]] = []
        for i in range(n):
            label = random.choice(label_names)
            sample_ids = split_index[label]
            sample_id = random.choice(sample_ids)
            result.append((split, label, sample_id))

        return result

    def get_split_size(self, split: str) -> int:
        if split not in self.split_stats:
            raise ValueError(f'Split "{split}" not found in the dataset.')
        return self.split_stats[split]

    def get_image_path(self, split: str, label: str, sample_id: str) -> str:
        for ext in ['.jpg', '.jpeg']:
            image_path = os.path.join(self._path, split, label, f'{sample_id}{ext}')
            if os.path.exists(image_path):
                return image_path
        raise FileNotFoundError(f'Image for sample id "{sample_id}" not found in {split}/{label}!')

    def load_image(self, split: str, label: str, sample_id: str) -> str:
        image_path = self.get_image_path(split, label, sample_id)
        if not os.path.exists(image_path):
            raise FileNotFoundError(f'Image "{image_path}" not found!')
        return cv2.imread(image_path)

    def get_annot_path(self, split: str, label: str, sample_id: str) -> str:
        return os.path.join(self._path, split, label, 'Label', f'{sample_id}.txt')

    def parse_annot(self, split: str, label: str, sample_id: str) -> List[Tuple[str, float, float, float, float]]:
        annot_path = self.get_annot_path(split, label, sample_id)
        with open(annot_path, 'r', encoding='utf-8') as f:
            lines = f.readlines()
        annots: List[Tuple[str, float, float, float, float]] = []
        for l in lines:
            items = l.split()
            if len(items) < 5:
                print(f"Skipping invalid annotation in {annot_path}: {l.strip()}")
                continue
            label_name = ' '.join(items[:-4])
            coords = [float(v) for v in items[-4:]]
            annots.append((label_name, *coords))
        return annots

    def convert(self, path: str) -> None:
        for split in self._index:
            split_path = os.path.join(path, split)
            images_path = os.path.join(split_path, 'images')
            labels_path = os.path.join(split_path, 'labels')
            Path(images_path).mkdir(parents=True, exist_ok=True)
            Path(labels_path).mkdir(parents=True, exist_ok=True)

            for label, sample_ids in tqdm(self._index[split].items(), desc='Converting to Yolo format', total=len(self._index[split])):
                assert len(sample_ids) == len(set(sample_ids))
                for sample_id in sample_ids:
                    image_path = self.get_image_path(split, label, sample_id)
                    new_image_path = os.path.join(images_path, f'{sample_id}.jpg')
                    annots = self.parse_annot(split, label, sample_id)
                    new_annot_path = os.path.join(labels_path, f'{sample_id}.txt')

                    # Debug statement to check the annotations
                    print(f"Annotations for {sample_id}: {annots}")

                    # Image needs to be loaded in order to read width and height
                    # which are required for coordinate normalization
                    image = self.load_image(split, label, sample_id)
                    h, w, _ = image.shape

                    # Conversion
                    converted_annot: List[Tuple[int, float, float, float, float]] = []
                    for label, x_min, y_min, x_max, y_max in annots:
                        label_index = self.label_lookup[label]
                        x_center = (x_min + x_max) / (2 * w)
                        y_center = (y_min + y_max) / (2 * h)
                        width = (x_max - x_min) / w
                        height = (y_max - y_min) / h

                        converted_annot.append((label_index, x_center, y_center, width, height))

                    # Save data
                    with open(new_annot_path, 'a', encoding='utf-8') as f:
                        converted_annot_lines = [' '.join([str(v) for v in row]) for row in converted_annot]
                        f.write('\n'.join(converted_annot_lines))
                        f.write('\n')

                    if not os.path.exists(new_image_path):
                        shutil.copy(image_path, new_image_path)

# Example usage:
# Make sure to set the path and debug variables
DATASET_PATH = '/kaggle/input/Project Dataset for Animal Prediction'
MASTER_PATH = '/kaggle/working/'
DEBUG = False

adapter = AnimalToYOLODatasetAdapter(
    path=DATASET_PATH,
    label_filter=['Horse'] if DEBUG else None
)

print(f'Total number of samples in the dataset is {len(adapter)}.')
print(f'Total number of classes in the dataset is {adapter.n_labels}.')
try:
    print(f'Train dataset size is {adapter.get_split_size("train")} (images). Test dataset size is {adapter.get_split_size("test")} (images)')
except ValueError as e:
    print(e)

adapter.convert(MASTER_PATH)

# Generate the YOLO config file
class_names = list(adapter.label_lookup.table.keys())
config = {
    'path': MASTER_PATH,
    'train': 'train/images',
    'val': 'test/images',
    'nc': len(class_names),  # Number of classes
    'names': class_names
}

# Print the config
print(config)

# Define the path where you want to save the config.yaml file
config_path = '/kaggle/working/config.yaml'

# Write the config dictionary to a YAML file
with open(config_path, 'w') as f:
    yaml.dump(config, f)

# Print a confirmation message
print(f'Config file saved to {config_path}')

Indexing train: 100%|██████████| 81/81 [00:05<00:00, 16.01sample/s]


Total number of samples in the dataset is 29144.
Total number of classes in the dataset is 81.
Train dataset size is 22610 (images). Test dataset size is 6534 (images)


Converting to Yolo format:   0%|          | 0/81 [00:00<?, ?it/s]

Annotations for ee577821df67a483: [('Spider', 8.73472, 3.6795649999999998, 1019.5466240000001, 361.02515)]
Annotations for 8c922ad0ea78fecf: [('Spider', 76.703734, 36.61824, 532.717382, 1009.0270720000001)]
Annotations for 81067426068b965f: [('Spider', 237.22803199999998, 233.995892, 808.9753599999999, 408.2457600000001)]
Annotations for 6904fd6dbcad110c: [('Spider', 234.24409599999998, 0.343905, 949.015552, 680.545092)]
Annotations for 347221a32e893e8e: [('Spider', 140.133916, 54.025216, 526.0235759999999, 938.9199359999999)]
Annotations for d6dd405ff27a5dca: [('Spider', 179.59423999999999, 25.269634000000003, 881.7285119999999, 647.319397)]
Annotations for 9ef3ccac95c80fba: [('Spider', 179.06688, 69.91027199999999, 761.335808, 673.4845439999999)]
Annotations for 2389878e316820e7: [('Spider', 186.13145600000001, 94.319616, 818.615296, 705.41184)]
Annotations for 65704399bc54a790: [('Spider', 0.282624, 178.831872, 1023.527936, 712.708608)]
Annotations for 87e3c106fdb434b4: [('Spider', 

Converting to Yolo format:   1%|          | 1/81 [00:03<04:57,  3.72s/it]

...

Annotations for 748840ac74952f77: [('Deer', 28.16, 64.626084, 537.6, 522.125901)]
Annotations for ab4243d1ca3ee659: [('Turkey', 0.0, 30.079872, 938.88, 575.360064)]
Annotations for 184c043f7a844d2e: [('Turkey', 113.92, 0.0, 1023.36, 682.3593460000001)]
Annotations for 1ba8879712cd7ba2: [('Turkey', 122.24, 0.0, 981.12, 767.360256)]
Annotations for bd6c91acf57d1675: [('Turkey', 246.612992, 0.0, 939.52, 679.1466)]
Annotations for 32e2e1b20a707755: [('Turkey', 0.0, 70.4, 682.3593460000001, 1023.36)]
Annotations for 1a79d315c1995e6d: [('Turkey', 0.0, 176.000256, 873.6, 628.479744), ('Turkey', 800.0, 71.03999999999999, 925.44, 190.07999999999998), ('Turkey', 908.16, 181.119744, 1023.36, 512.000256), ('Turkey', 909.44, 0.0, 983.68, 103.040256)]
Annotations for 9c19ec1636a29495: [('Turkey', 86.4, 44.209224, 501.12, 518.336896)]
Annotations for 350fd0cea87ac954: [('Turkey', 0.0, 213.76, 554.216935, 1023.36)]
Annotations for 54f1e0ff2c11742e: [('Turkey', 88.96, 0.0, 1023.36, 682.3593460000001)]


Converting to Yolo format:  99%|█████████▉| 80/81 [06:27<00:03,  3.62s/it]

Annotations for 5a439ef75eb54bfa: [('Turkey', 104.96, 290.55974399999997, 743.68, 705.2797439999999)]
Annotations for d14283d33bebe1a7: [('Turkey', 0.0, 21.76, 838.4, 1020.16)]
Annotations for bd2b17ef8d411bb7: [('Sea lion', 10.999808, 81.000086, 940.9996800000001, 705.000304)]
Annotations for 8e660cc701e0f415: [('Sea lion', 69.12, 0.0, 874.24, 584.754302)]
Annotations for 1342e735b93cc28c: [('Sea lion', 10.88, 76.110212, 1023.36, 516.783538)]
Annotations for 205c880717907a08: [('Sea lion', 256.64, 83.172986, 934.4, 610.3602830000001)]
Annotations for ea87e22457b6bc9f: [('Sea lion', 0.0, 161.459834, 509.44, 682.3593460000001), ('Sea lion', 588.16, 202.465105, 1023.36, 597.785505)]
Annotations for debf8c2711424b6f: [('Sea lion', 386.048, 210.77507999999997, 1022.976, 616.976592)]
Annotations for 89d5f49ef0a9d606: [('Sea lion', 265.6, 93.544363, 1022.08, 682.3593460000001)]
Annotations for 0b9132ad6f49f8ec: [('Sea lion', 234.24, 0.0, 1023.36, 682.3593460000001)]
Annotations for 22e06ab3e

Converting to Yolo format: 100%|██████████| 81/81 [06:30<00:00,  4.82s/it]

Annotations for 882d5e9f462ac594: [('Sea lion', 497.28, 309.97734299999996, 896.64, 650.056329)]
Annotations for cd31c86e18d4f57b: [('Sea lion', 152.32, 166.585066, 819.2, 649.041923)]
Annotations for d1411ca29cc1e057: [('Sea lion', 60.999680000000005, 48.99988, 810.0003839999999, 734.99986)]
Annotations for 45e05688c6c41d45: [('Sea lion', 109.44, 254.586399, 669.44, 514.290261)]
Annotations for f0e21fc75d0edf5f: [('Sea lion', 389.76, 313.949146, 856.96, 651.605222)]
Annotations for 2ca7ff0ceea50010: [('Sea lion', 423.19974400000007, 130.32338000000001, 1023.2002560000001, 648.4196840000001)]
Annotations for da66deab24f55705: [('Sea lion', 49.92, 10.250016, 985.6, 607.938912)]
Annotations for 8b786dd64a8d0348: [('Sea lion', 77.52704, 127.59396000000002, 1022.385152, 796.251008)]
Annotations for 7a33724d14b276af: [('Sea lion', 206.72, 88.959744, 651.52, 642.560256)]
Annotations for 1bd4988852601bd9: [('Sea lion', 99.84, 135.190288, 975.36, 674.030161)]
{'path': '/kaggle/working/', 'trai

In [9]:
!wandb login --relogin 0eec33137144ec1e75b97fd79f1bd99f3a12e5f4


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [10]:
# Load a pretrained YOLO model (recommended for training)
model = YOLO('yolov8n.pt') 
model.to('cuda').half()

# Train the model using the processed dataset
results = model.train(
    data='config.yaml',
    epochs=80 if not DEBUG else 1,
    optimizer='Adam',
    val=True,
    batch=176, 
    imgsz=640,
    device=[0, 1],  # Use both GPUs (IDs 0 and 1)
    lr0=0.001,
    lrf=0.0005
)

# Evaluate the model's performance on the validation set
results = model.val()

print(results)

100%|██████████| 6.25M/6.25M [00:00<00:00, 72.8MB/s]


Ultralytics YOLOv8.2.48 🚀 Python-3.10.13 torch-2.3.1+cu121 CUDA:0 (Tesla T4, 15102MiB)
                                                            CUDA:1 (Tesla T4, 15102MiB)
engine/trainer: task=detect, mode=train, model=yolov8n.pt, data=config.yaml, epochs=80, time=None, patience=100, batch=176, imgsz=640, save=True, save_period=-1, cache=False, device=[0, 1], workers=8, project=None, name=train, exist_ok=False, pretrained=True, optimizer=Adam, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=Fals

100%|██████████| 755k/755k [00:00<00:00, 14.9MB/s]
2024-07-02 20:57:03,733	INFO util.py:124 -- Outdated packages:
  ipywidgets==7.7.1 found, needs ipywidgets>=8
Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-07-02 20:57:04,682	INFO util.py:124 -- Outdated packages:
  ipywidgets==7.7.1 found, needs ipywidgets>=8
Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


Overriding model.yaml nc=80 with nc=81

                   from  n    params  module                                       arguments                     
  0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
  1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
  2                  -1  1      7360  ultralytics.nn.modules.block.C2f             [32, 32, 1, True]             
  3                  -1  1     18560  ultralytics.nn.modules.conv.Conv             [32, 64, 3, 2]                
  4                  -1  2     49664  ultralytics.nn.modules.block.C2f             [64, 64, 2, True]             
  5                  -1  1     73984  ultralytics.nn.modules.conv.Conv             [64, 128, 3, 2]               
  6                  -1  2    197632  ultralytics.nn.modules.block.C2f             [128, 128, 2, True]           
  7                  -1  1    295424  ultralytic

wandb: Currently logged in as: surya-21mic7196 (surya-vitap). Use `wandb login --relogin` to force relogin
wandb: wandb version 0.17.3 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.17.0
wandb: Run data is saved locally in /kaggle/working/wandb/run-20240702_205733-r29ajx6s
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run train
wandb: ⭐️ View project at https://wandb.ai/surya-vitap/YOLOv8
wandb: 🚀 View run at https://wandb.ai/surya-vitap/YOLOv8/runs/r29ajx6s


...

                   all       6032       7618      0.676      0.647      0.689      0.579
                Spider        207        213      0.913      0.941      0.976      0.837
                Parrot        180        203      0.839      0.837      0.891      0.784
              Scorpion         44         44      0.869      0.757       0.86      0.753
            Sea turtle         87        104      0.662      0.226      0.589      0.488
                Cattle        171        209      0.873      0.263      0.581      0.511
                   Fox         69         72      0.762      0.792      0.831      0.739
              Hedgehog         49         52      0.787      0.846      0.924      0.795
                Turtle          5          7          1          0     0.0101    0.00758
               Cheetah         35         39      0.648      0.641      0.713      0.631
                 Snake        213        219      0.831      0.913      0.928      0.729
                 Shar

wandb:                                                                                
wandb: 
wandb: Run history:
wandb:                  lr/pg0 █▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:                  lr/pg1 ▃███▇▇▇▇▇▇▆▆▆▆▆▅▅▅▅▅▅▄▄▄▄▄▃▃▃▃▃▃▂▂▂▂▂▁▁▁
wandb:                  lr/pg2 ▃███▇▇▇▇▇▇▆▆▆▆▆▅▅▅▅▅▅▄▄▄▄▄▃▃▃▃▃▃▂▂▂▂▂▁▁▁
wandb:        metrics/mAP50(B) ▁▂▃▄▄▅▅▆▆▆▆▆▆▇▆▇▇▇▇▇▇█▇▇████████████████
wandb:     metrics/mAP50-95(B) ▁▂▃▄▄▄▅▅▅▅▆▆▆▆▆▆▇▇▇▇▇▇▇▇▇█▇█████████████
wandb:    metrics/precision(B) ▁▂▃▄▃▅▄▅▅▅▅▅▆▇▆▇▇▆▇▇▇▇▇▇▇▇█████▇██▇████▇
wandb:       metrics/recall(B) ▁▃▃▄▅▄▆▆▆��▆▆▆▆▆▆▇▇▇▇▇▇▇▇▇▇▇█████████████
wandb:            model/GFLOPs ▁
wandb:        model/parameters ▁
wandb: model/speed_PyTorch(ms) ▁
wandb:          train/box_loss ▇█▇▇▆▆▆▆▆▆▆▅▅▅▅▅▅▅▅▅▅▅▅▄▄▄▄▄▄▄▄▄▄▄▃▂▁▁▁▁
wandb:          train/cls_loss █▅▄▄▄▃▃▃▃▃▃▃▃▃▃▃▃▃▃▃▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▁▁▁▁▁
wandb:          train/dfl_loss ▇█▇▇▆▆▆▆▆▅▅▅▅▅▅▅▅▅▅▅▅▅▄▄▄▄▄▄▄▄▄▄▄▄▃▂▂▂▁▁
wandb:            val/box_loss █▇▅▅▅▄▄▄▄▃▃▃▃▃▃▂▂▂▂▂▂▂▂▂▂▁▂▁▁▁▁▁▁▁

Ultralytics YOLOv8.2.48 🚀 Python-3.10.13 torch-2.3.1+cu121 CUDA:0 (Tesla T4, 15102MiB)
                                                            CUDA:1 (Tesla T4, 15102MiB)
Model summary (fused): 168 layers, 3160775 parameters, 0 gradients, 8.8 GFLOPs


val: Scanning /kaggle/working/test/labels.cache... 6032 images, 0 backgrounds, 0 corrupt: 100%|██████████| 6032/6032 [00:00<?, ?it/s]
/opt/conda/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   3%|▎         | 1/35 [00:04<02:32,  4.49s/it]Exception in thread Thread-8 (plot_images):
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
Exception in thread Thread-9 (plot_images):
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/opt/conda/lib/python3.10/threading.py", line 953, in run
    self.run()
  File "/opt/conda/lib/python3.10/threading.py", line 953, in run
    self._ta

                   all       6032       7618      0.676      0.647      0.689       0.58
                Spider        207        213      0.913      0.941      0.976      0.837
                Parrot        180        203      0.838      0.837       0.89      0.784
              Scorpion         44         44       0.87      0.759       0.86      0.752
            Sea turtle         87        104      0.665      0.231       0.59      0.487
                Cattle        171        209      0.872      0.261      0.581      0.511
                   Fox         69         72      0.762      0.792      0.831       0.74
              Hedgehog         49         52      0.786      0.849      0.923      0.798
                Turtle          5          7          1          0     0.0101    0.00754
               Cheetah         35         39      0.648      0.641      0.713      0.633
                 Snake        213        219       0.83      0.913      0.928       0.73
                 Shar

In [11]:
!zip -r results.zip /kaggle/working/

/opt/conda/lib/python3.10/pty.py:89: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid, fd = os.forkpty()


  adding: kaggle/working/ (stored 0%)
  adding: kaggle/working/runs/ (stored 0%)
  adding: kaggle/working/runs/detect/ (stored 0%)
  adding: kaggle/working/runs/detect/train2/ (stored 0%)
  adding: kaggle/working/runs/detect/train2/confusion_matrix.png (deflated 16%)
  adding: kaggle/working/runs/detect/train2/F1_curve.png (deflated 9%)
  adding: kaggle/working/runs/detect/train2/PR_curve.png (deflated 7%)
  adding: kaggle/working/runs/detect/train2/confusion_matrix_normalized.png (deflated 17%)
  adding: kaggle/working/runs/detect/train2/P_curve.png (deflated 8%)
  adding: kaggle/working/runs/detect/train2/R_curve.png (deflated 9%)
  adding: kaggle/working/runs/detect/train/ (stored 0%)
  adding: kaggle/working/runs/detect/train/train_batch8681.jpg (deflated 8%)
  adding: kaggle/working/runs/detect/train/val_batch2_labels.jpg (deflated 8%)
  adding: kaggle/working/runs/detect/train/val_batch0_labels.jpg (deflated 12%)
  adding: kaggle/working/runs/detect/train/val_batch1_labels.jpg (d

In [12]:
!ls

__notebook__.ipynb  results.zip  test	wandb
config.yaml	    runs	 train	yolov8n.pt


In [13]:
from IPython.display import FileLink
FileLink(r'results.zip')

/kaggle/working/results.zip